## Импорт библиотек

In [1]:
import os
import numpy as np
import pandas as pd
from tqdm import tqdm
import matplotlib.pyplot as plt
import json

## Функции используемые для создания данных для обучения

In [7]:
def save_json_dataset(dset):
    number_samples = 1024
    for i in range(int(np.floor(len(dset) / number_samples))):
        with open(f'dp vetrical zones/vertical_center/dataset_{i}.json', 'w') as file:
            if i == np.floor(len(dset) / number_samples) - 1:
                json.dump(dset[i * number_samples:], file)
                print(f'dataset_{i} сохранен')
            else:
                json.dump(dset[i * number_samples:i * number_samples + number_samples], file)
                print(f'dataset_{i} сохранен')

def save_json_dataset_wall(dset):
    number_samples = 1024
    for i in range(int(np.floor(len(dset) / number_samples))):
        with open(f'dp vetrical zones/vertical_wall/dataset_{i}.json', 'w') as file:
            if i == np.floor(len(dset) / number_samples) - 1:
                json.dump(dset[i * number_samples:], file)
                print(f'dataset_{i} сохранен')
            else:
                json.dump(dset[i * number_samples:i * number_samples + number_samples], file)
                print(f'dataset_{i} сохранен')
             

def heigh_of_col(mrx, index):
    column = mrx[:, index]
    mask = column != -1
    count_non_negative = np.sum(mask)
    return count_non_negative

def max_width_spinneret(matrix_array):
    
    # Находим индексы элементов, не равных -1, для каждой строки 
    non_negative_indices = (matrix_array != -1)                          
                                                                            
    # Считаем количество элементов, не равных -1, для каждой строки      
    count_non_negative_elements = np.sum(non_negative_indices, axis=1)   
                                                                            
    # Находим индекс строки с максимальным количеством элементов, не равных -1
    max_row_index = np.argmax(count_non_negative_elements)
    max_width = count_non_negative_elements[max_row_index]
    
    return max_width

def width_row(matrix_array, row):
    # Находим индексы элементов, не равных -1, в выбранной строке
    non_negative_indices_in_selected_row = (matrix_array[row] != -1)

    # Считаем количество элементов, не равных -1, в выбранной строке
    count_non_negative_elements_in_selected_row = np.sum(non_negative_indices_in_selected_row)
    
    return count_non_negative_elements_in_selected_row

def length_to_elements(matrix_array, row, column):
    selected_row_part = matrix_array[row, :column + 1]
    non_negative_indices_in_selected_row_part = (selected_row_part != -1)
    count_non_negative_elements_in_selected_row_part = np.sum(non_negative_indices_in_selected_row_part)
    
    return count_non_negative_elements_in_selected_row_part

def process_matrix(mrx, dataset):
    
    max_width = max_width_spinneret(mrx) 

    for row in range(1, 201):
        for col in range(0, 203):
            if mrx[row, col] != -1:
                submrx = mrx[row - 1 : row + 1, col - 1: col + 2]
                
                wdh_pr = width_row(mrx, row - 1)
                
                wdh_r = width_row(mrx, row)
                lng = length_to_elements(mrx, row, col)
                hgt_c = heigh_of_col(mrx, col)

                if row == 200:
                    wdh_next = width_row(mrx, row)
                else:
                    wdh_next = width_row(mrx, row + 1)     
                
                central = submrx[1, 1]
                outer = []
                d4_d1 = wdh_pr / max_width
                d2_d1 = wdh_r / max_width
                d3_d2 = lng / wdh_r
                d5_d1 = wdh_next / max_width
                dyn_dy = (row + 1) / hgt_c
                outer.append(row)
                outer.append(col)
                for x_offset, y_offset in [(0, 0), (0, 1), (0, 2)]:
                    outer_value = submrx[x_offset, y_offset]
                    outer.append(outer_value)

                outer.append(d2_d1)
                outer.append(d3_d2)
                outer.append(d4_d1)
                outer.append(dyn_dy)
                outer.append(d5_d1)
                outer.append(central)
                dataset.append(outer)

                
                          

   

## Получение названий файлов датасета

In [8]:
datasets = []

for filename in os.listdir('CSV dataset'):
    datasets.append(f'CSV dataset/{filename}')
print(datasets)    
   

['CSV dataset/Dataset_0.csv', 'CSV dataset/Dataset_1.csv', 'CSV dataset/Dataset_3.csv', 'CSV dataset/Dataset_4.csv']


In [ ]:
count = 0
for path in datasets:
    df = pd.read_csv(path)
    columns = list(df.columns)
    for column in columns[2:]:
        df.loc[(df['x'] == 1.01) & (df['y'] == 0), column] = -1
        df.loc[(df['x'] == -1.01) & (df['y'] == 0), column] = -1
    path_new = f'CSV dataset/Dataset{count}.csv'
    df.to_csv(path_new, index = False, na_rep = 'NaN')
    count += 1   

## Создание матриц для каждого файла из всех столбцов

In [9]:
def create_matrixes(columns, df, matrixes):
    for column in columns:
        matrix = pd.pivot_table(df, values=column, index='y', columns='x', fill_value=-1)
        mrx = np.flipud(matrix.to_numpy())
        matrixes.append(mrx)

In [10]:
step_x = 0.01
step_y = 0.01
columns = []
matrixes = []

df = pd.read_csv(datasets[0])
columns.append(list(df.columns[2:]))
print(len(columns))
create_matrixes(columns[0][0:2], df, matrixes)

1


In [12]:
matrixes

[array([[-1.00000000e+00,  0.00000000e+00,  5.87950710e-04, ...,
          5.87964604e-04,  0.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00,  0.00000000e+00,  5.87659096e-04, ...,
          5.87682593e-04,  0.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00,  0.00000000e+00,  5.87365769e-04, ...,
          5.87335908e-04,  0.00000000e+00, -1.00000000e+00],
        ...,
        [-1.00000000e+00, -1.00000000e+00, -1.00000000e+00, ...,
         -1.00000000e+00, -1.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00, -1.00000000e+00, -1.00000000e+00, ...,
         -1.00000000e+00, -1.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00, -1.00000000e+00, -1.00000000e+00, ...,
         -1.00000000e+00, -1.00000000e+00, -1.00000000e+00]]),
 array([[-1.00000000e+00,  0.00000000e+00,  5.87666717e-04, ...,
          5.87641893e-04,  0.00000000e+00, -1.00000000e+00],
        [-1.00000000e+00,  0.00000000e+00,  5.87376563e-04, ...,
          5.87337556e-04,  0.00000000e

In [13]:
len(matrixes)

2

In [11]:
dset_example = []
df = pd.DataFrame(columns=['row','col','v1','v2','v3', 'd2_d1', 'd3_d2', 'd4_d1', 'dyn_dy', 'd5_d1', 'central'])
process_matrix(matrixes[0], df)
print(df)
len(dset_example)

C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset.append(outer)
C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset.append(outer)
C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset.append(outer)
C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  dataset.append(outer)
C:\Users\190782\AppData\Local\Temp\ipykernel_15824\3620846579.py:99: FutureWarning: The frame.ap

KeyboardInterrupt: 

In [12]:
dset = []
for mrx in matrixes:
    process_matrix(mrx, dset)
df = pd.DataFrame(dset)
columns = ['row','col','v1','v2','v3', 'd2_d1', 'd3_d2', 'd4_d1', 'dyn_dy', 'd5_d1', 'central']
df.columns = columns
df.to_csv('DS3.csv', index=False)
df
    

row  col        v1            v2            v3     d2_d1     d3_d2  \
0        1    1 -1.000000  0.000000e+00  5.879507e-04  1.000000  0.004975   
1        1    2  0.000000  5.879507e-04  1.169852e-03  1.000000  0.009950   
2        1    3  0.000588  1.169852e-03  1.746375e-03  1.000000  0.014925   
3        1    4  0.001170  1.746375e-03  2.318073e-03  1.000000  0.019900   
4        1    5  0.001746  2.318073e-03  2.882437e-03  1.000000  0.024876   
...    ...  ...       ...           ...           ...       ...       ...   
68425  200  102  0.590429  5.595119e-01  5.132532e-01  0.054726  0.636364   
68426  200  103  0.559512  5.132532e-01  3.861490e-01  0.054726  0.727273   
68427  200  104  0.513253  3.861490e-01  2.135005e-01  0.054726  0.818182   
68428  200  105  0.386149  2.135005e-01  8.597557e-16  0.054726  0.909091   
68429  200  106  0.213500  8.597557e-16 -1.000000e+00  0.054726  1.000000   

          d4_d1    dyn_dy     d5_d1       central  
0      1.000000  0.011696  1.000000  0.000000e+00  
1      1.000000  0.011696  1.000000  5.876591e-04  
2      1.000000  0.011696  1.000000  1.169337e-03  
3      1.000000  0.011696  1.000000  1.745492e-03  
4      1.000000  0.011696  1.000000  2.317001e-03  
...         ...       ...       ...           ...  
68425  0.054726  1.000000  0.054726  5.691741e-01  
68426  0.054726  1.000000  0.054726  4.987660e-01  
68427  0.054726  1.000000  0.054726  3.935971e-01  
68428  0.054726  1.000000  0.054726  2.260050e-01  
68429  0.054726  1.000000  0.054726  1.274808e-15  

[68430 rows x 11 columns]

In [13]:
print(len(dset))




68430


In [ ]:
type(matrixes[0])

In [ ]:
save_json_dataset(dset)
save_json_dataset_wall(dset_wall)

In [ ]:
prediction_values = []
input_values = []
for item in tqdm(dset):
    prediction_values.append(item['output'])
    input_values.append(item['input'])

    